This is a Jupyter Notebook that can be used with any book found at Project Gutenberg. However, manual inspection of the book is necessary to check the book display in there. 

The first part of the notebook (A), covers data acquisition. The second part (B), covers cleaning and preprocessing and saving data for later on counting words (so, difficult character removal >> tokenization >> lower casing >> punctuation removal >> stop word removal). The third part (C), covers clearning and preprocessing data for later on applying NER (so, not following the previous pipeline, but just removing noise characters). 

# A. Data Acquisition

### 1. We import the libraries

In [55]:
from urllib import request
from bs4 import BeautifulSoup

import re
import pandas as pd
import string

import nltk 
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

### 2. We get the data

In [56]:
url = "https://www.gutenberg.org/cache/epub/580/pg580.txt" #we create a variable with the url of our target book.This url 
                                                           #contains text of "The Picwick Papers" by Charles Dickens

In [57]:
response = request.urlopen(url)
raw = response.read().decode("utf-8")

### 3. We prettify the data

In [58]:
soup = BeautifulSoup(raw, "html.parser")

#print(soup.prettify())

In [59]:
data = soup.prettify()
#data

### 4. We select the data

In [60]:
text = re.search("START OF THE PROJECT GUTENBERG EBOOK THE PICKWICK PAPERS", data)

In [61]:
text

<re.Match object; span=(748, 804), match='START OF THE PROJECT GUTENBERG EBOOK THE PICKWICK>

In [62]:
text_2 = re.search("END OF THE PROJECT GUTENBERG EBOOK", data)
text_2

<re.Match object; span=(1783956, 1783990), match='END OF THE PROJECT GUTENBERG EBOOK'>

In [63]:
text_3 = data[804:1783956]

In [64]:
text_3

' ***\r\n\r\n\r\n\r\nProduced by Jo Churcher, and David Widger\r\n\r\n\r\n\r\nTHE PICKWICK PAPERS\r\n\r\n\r\nBy Charles Dickens\r\n\r\n\r\n\r\nCONTENTS\r\n\r\n\r\nTHE POSTHUMOUS PAPERS OF THE PICKWICK CLUB\r\n\r\n\r\nCHAPTER I. \xa0\xa0THE PICKWICKIANS\r\n\r\nCHAPTER II. \xa0\xa0THE FIRST DAY’S JOURNEY, AND THE FIRST EVENING’S\r\nADVENTURES; WITH THEIR CONSEQUENCES\r\n\r\nCHAPTER III. \xa0\xa0A NEW ACQUAINTANCE--THE STROLLER’S TALE; A DISAGREEABLE\r\nINTERRUPTION, AND AN UNPLEASANT ENCOUNTER\r\n\r\nCHAPTER IV. \xa0\xa0A FIELD DAY AND BIVOUAC--MORE NEW FRIENDS\r\n\r\nCHAPTER V. \xa0\xa0A SHORT ONE--SHOWING, AMONG OTHER MATTERS\r\n\r\nCHAPTER VI. \xa0\xa0AN OLD-FASHIONED CARD-PARTY--THE CLERGYMAN’S VERSES\r\n\r\nCHAPTER VII. \xa0\xa0HOW MR. WINKLE, INSTEAD OF SHOOTING AT THE PIGEON\r\n\r\nCHAPTER VIII. \xa0\xa0STRONGLY ILLUSTRATIVE OF THE POSITION\r\n\r\nCHAPTER IX. \xa0\xa0A DISCOVERY AND A CHASE\r\n\r\nCHAPTER X. \xa0\xa0CLEARING UP ALL DOUBTS (IF ANY EXISTED)\r\n\r\nCHAPTER XI. \xa0\x

In [65]:
text_4 = re.search("THE POSTHUMOUS PAPERS OF THE PICKWICK CLUB\r\n\r\n\r\n\r\nCHAPTER I. THE PICKWICKIANS\r\n\r\n", text_3)
text_4

<re.Match object; span=(11818, 11899), match='THE POSTHUMOUS PAPERS OF THE PICKWICK CLUB\r\n\r\>

In [66]:
data = text_3[11818:]
data

'THE POSTHUMOUS PAPERS OF THE PICKWICK CLUB\r\n\r\n\r\n\r\nCHAPTER I. THE PICKWICKIANS\r\n\r\nThe first ray of light which illumines the gloom, and converts into a\r\ndazzling brilliancy that obscurity in which the earlier history of the\r\npublic career of the immortal Pickwick would appear to be involved, is\r\nderived from the perusal of the following entry in the Transactions of\r\nthe Pickwick Club, which the editor of these papers feels the highest\r\npleasure in laying before his readers, as a proof of the careful\r\nattention, indefatigable assiduity, and nice discrimination, with which\r\nhis search among the multifarious documents confided to him has been\r\nconducted.\r\n\r\n‘May 12, 1827. Joseph Smiggers, Esq., P.V.P.M.P.C. [Perpetual Vice-\r\nPresident--Member Pickwick Club], presiding. The following resolutions\r\nunanimously agreed to:--\r\n\r\n‘That this Association has heard read, with feelings of unmingled\r\nsatisfaction, and unqualified approval, the paper communica

Let's clean that even more. Let's get rid of all the first part containing the chapter index

# B) Clearning and Pre-Processing. Word counts

This part is very much depending on what we want to do with our data. I have selected to follow the pipeline " difficult character removal >> tokenization >> lower casing >> punctuation removal >> stop word removal". But this is very personal and totally up to us. This cleaning and preprocessing part is taylor-made for counting words (NER will follow a different cleaning and pre-processing process). 

**1. Difficult character removal**

In [83]:
text = re.sub(r'--+', ' ', data)

In [84]:
text_1 = re.sub(r'[‘’“”]', " ", text)

In [85]:
text_1

'THE POSTHUMOUS PAPERS OF THE PICKWICK CLUB\r\n\r\n\r\n\r\nCHAPTER I. THE PICKWICKIANS\r\n\r\nThe first ray of light which illumines the gloom, and converts into a\r\ndazzling brilliancy that obscurity in which the earlier history of the\r\npublic career of the immortal Pickwick would appear to be involved, is\r\nderived from the perusal of the following entry in the Transactions of\r\nthe Pickwick Club, which the editor of these papers feels the highest\r\npleasure in laying before his readers, as a proof of the careful\r\nattention, indefatigable assiduity, and nice discrimination, with which\r\nhis search among the multifarious documents confided to him has been\r\nconducted.\r\n\r\n May 12, 1827. Joseph Smiggers, Esq., P.V.P.M.P.C. [Perpetual Vice-\r\nPresident Member Pickwick Club], presiding. The following resolutions\r\nunanimously agreed to: \r\n\r\n That this Association has heard read, with feelings of unmingled\r\nsatisfaction, and unqualified approval, the paper communicate

**2. Tokenization**

In [97]:
tokens = word_tokenize(text_1)

In [98]:
tokens

['THE',
 'POSTHUMOUS',
 'PAPERS',
 'OF',
 'THE',
 'PICKWICK',
 'CLUB',
 'CHAPTER',
 'I',
 '.',
 'THE',
 'PICKWICKIANS',
 'The',
 'first',
 'ray',
 'of',
 'light',
 'which',
 'illumines',
 'the',
 'gloom',
 ',',
 'and',
 'converts',
 'into',
 'a',
 'dazzling',
 'brilliancy',
 'that',
 'obscurity',
 'in',
 'which',
 'the',
 'earlier',
 'history',
 'of',
 'the',
 'public',
 'career',
 'of',
 'the',
 'immortal',
 'Pickwick',
 'would',
 'appear',
 'to',
 'be',
 'involved',
 ',',
 'is',
 'derived',
 'from',
 'the',
 'perusal',
 'of',
 'the',
 'following',
 'entry',
 'in',
 'the',
 'Transactions',
 'of',
 'the',
 'Pickwick',
 'Club',
 ',',
 'which',
 'the',
 'editor',
 'of',
 'these',
 'papers',
 'feels',
 'the',
 'highest',
 'pleasure',
 'in',
 'laying',
 'before',
 'his',
 'readers',
 ',',
 'as',
 'a',
 'proof',
 'of',
 'the',
 'careful',
 'attention',
 ',',
 'indefatigable',
 'assiduity',
 ',',
 'and',
 'nice',
 'discrimination',
 ',',
 'with',
 'which',
 'his',
 'search',
 'among',
 'the'

In [99]:
type(tokens)

list

**3. Lower casing**

In [100]:
lower_tokens = []

for i in tokens:
    lower_tokens.append(i.lower()) 

In [101]:
lower_tokens

['the',
 'posthumous',
 'papers',
 'of',
 'the',
 'pickwick',
 'club',
 'chapter',
 'i',
 '.',
 'the',
 'pickwickians',
 'the',
 'first',
 'ray',
 'of',
 'light',
 'which',
 'illumines',
 'the',
 'gloom',
 ',',
 'and',
 'converts',
 'into',
 'a',
 'dazzling',
 'brilliancy',
 'that',
 'obscurity',
 'in',
 'which',
 'the',
 'earlier',
 'history',
 'of',
 'the',
 'public',
 'career',
 'of',
 'the',
 'immortal',
 'pickwick',
 'would',
 'appear',
 'to',
 'be',
 'involved',
 ',',
 'is',
 'derived',
 'from',
 'the',
 'perusal',
 'of',
 'the',
 'following',
 'entry',
 'in',
 'the',
 'transactions',
 'of',
 'the',
 'pickwick',
 'club',
 ',',
 'which',
 'the',
 'editor',
 'of',
 'these',
 'papers',
 'feels',
 'the',
 'highest',
 'pleasure',
 'in',
 'laying',
 'before',
 'his',
 'readers',
 ',',
 'as',
 'a',
 'proof',
 'of',
 'the',
 'careful',
 'attention',
 ',',
 'indefatigable',
 'assiduity',
 ',',
 'and',
 'nice',
 'discrimination',
 ',',
 'with',
 'which',
 'his',
 'search',
 'among',
 'the'

**4. Punctuation**

In [102]:
 string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [103]:
punctuation_free = []
punctuation_free = [token for token in lower_tokens if token not in string.punctuation]

In [104]:
punctuation_free

['the',
 'posthumous',
 'papers',
 'of',
 'the',
 'pickwick',
 'club',
 'chapter',
 'i',
 'the',
 'pickwickians',
 'the',
 'first',
 'ray',
 'of',
 'light',
 'which',
 'illumines',
 'the',
 'gloom',
 'and',
 'converts',
 'into',
 'a',
 'dazzling',
 'brilliancy',
 'that',
 'obscurity',
 'in',
 'which',
 'the',
 'earlier',
 'history',
 'of',
 'the',
 'public',
 'career',
 'of',
 'the',
 'immortal',
 'pickwick',
 'would',
 'appear',
 'to',
 'be',
 'involved',
 'is',
 'derived',
 'from',
 'the',
 'perusal',
 'of',
 'the',
 'following',
 'entry',
 'in',
 'the',
 'transactions',
 'of',
 'the',
 'pickwick',
 'club',
 'which',
 'the',
 'editor',
 'of',
 'these',
 'papers',
 'feels',
 'the',
 'highest',
 'pleasure',
 'in',
 'laying',
 'before',
 'his',
 'readers',
 'as',
 'a',
 'proof',
 'of',
 'the',
 'careful',
 'attention',
 'indefatigable',
 'assiduity',
 'and',
 'nice',
 'discrimination',
 'with',
 'which',
 'his',
 'search',
 'among',
 'the',
 'multifarious',
 'documents',
 'confided',
 '

**5. Stop words**

In [105]:
stop_words = set(stopwords.words("english"))

clean = [token for token in punctuation_free if token not in stop_words]

super_clean = ' '.join(clean)

In [106]:
super_clean

'posthumous papers pickwick club chapter pickwickians first ray light illumines gloom converts dazzling brilliancy obscurity earlier history public career immortal pickwick would appear involved derived perusal following entry transactions pickwick club editor papers feels highest pleasure laying readers proof careful attention indefatigable assiduity nice discrimination search among multifarious documents confided conducted may 12 1827 joseph smiggers esq. p.v.p.m.p.c perpetual vice- president member pickwick club presiding following resolutions unanimously agreed association heard read feelings unmingled satisfaction unqualified approval paper communicated samuel pickwick esq. g.c.m.p.c general chairman member pickwick club entitled speculations source hampstead ponds observations theory tittlebats association hereby return warmest thanks said samuel pickwick esq. g.c.m.p.c. association deeply sensible advantages must accrue cause science production adverted less unwearied researches

**6. Saving things into a text file**

In [107]:
with open("The Pickwick Papers_word_counts.txt", "w", encoding = "utf-8") as f:
    f.write(super_clean)

# C) Cleaning and Pre-Processing. NER

In order to use Spacy pipelines for NER (Name Entity Recognition), we need to keep the text in its oringinal form and only remove noise characters such as r/n/n/r. So lets go back to the data variable and lets do that!

In [52]:
# Remove carriage returns, line feeds, and other escape codes
clean_text = re.sub(r'[\r\n]+', ' ', data)  # replace newlines with a space
clean_text = clean_text.replace('\xa0', ' ')  # remove non-breaking spaces

# Optionally, collapse multiple spaces and strip
clean_text = re.sub(r'\s+', ' ', clean_text).strip()

In [53]:
clean_text

'THE POSTHUMOUS PAPERS OF THE PICKWICK CLUB CHAPTER I. THE PICKWICKIANS The first ray of light which illumines the gloom, and converts into a dazzling brilliancy that obscurity in which the earlier history of the public career of the immortal Pickwick would appear to be involved, is derived from the perusal of the following entry in the Transactions of the Pickwick Club, which the editor of these papers feels the highest pleasure in laying before his readers, as a proof of the careful attention, indefatigable assiduity, and nice discrimination, with which his search among the multifarious documents confided to him has been conducted. ‘May 12, 1827. Joseph Smiggers, Esq., P.V.P.M.P.C. [Perpetual Vice- President--Member Pickwick Club], presiding. The following resolutions unanimously agreed to:-- ‘That this Association has heard read, with feelings of unmingled satisfaction, and unqualified approval, the paper communicated by Samuel Pickwick, Esq., G.C.M.P.C. [General Chairman--Member Pi

In [54]:
with open("The Pickwick Papers_NER.txt", "w", encoding = "utf-8") as f:
    f.write(clean_text)